In [158]:
import numpy as np
from nltk.stem import WordNetLemmatizer
import random
import theano 
import theano.tensor as T
import brown
from bs4 import BeautifulSoup as bs
import nltk
import matplotlib.pyplot as plt
%matplotlib inline

In [159]:
positive_reviews = bs(open('datasets/positive.review').read())
positive_reviews = positive_reviews.findAll('review_text')

In [160]:
stopwords = set([word.strip() for word in open('datasets/stopwords.txt')])
stopwords = stopwords.union({
    'introduction', 'edition', 'series', 'application',
    'approach', 'card', 'access', 'package', 'plus', 'etext',
    'brief', 'vol', 'fundamental', 'guide', 'essential', 'printed',
'third', 'second', 'fourth', })
def myCustomTokenizer(line):
    line = line.lower()
    words = nltk.tokenize.word_tokenize(line)
    words = [word for word in words if word not in stopwords]
    lemmatizer = WordNetLemmatizer()
    words = [lemmatizer.lemmatize(word) for word in words]
    words = [word for word in words if len(word)>2]
    words = [word for word in words if not any(c.isdigit() for c in word)]
    return words
word2idx = {'START':0,'END':1}
current = 2
sentences = []
for review in positive_reviews:
    review = review.text.lower()
    tokens = myCustomTokenizer(review)
    for token in tokens:
        if token not in word2idx:
            word2idx[token] = current
            current += 1
        sentences.append(word2idx[token])

In [161]:
V = len(word2idx)
N = len(sentences)
D = 100

In [176]:
class bigram():
    def __init__(self,D,V):
        #dimension of word embedding layer
        self.D = D
        self.V = V
    def init_weight(self,Mi,Mo):
        return np.random.randn(Mi,Mo)
    def plot_graph(costs):
        plt.plot(costs)
    def fit(self,X,alpha=10e-5,print_period=10,mu=0.99,activation=T.nnet.sigmoid,batchsize = 500):
        
        #initializing all weights
        V = self.V
        D = self.D
        self.f = activation
        
        #iniitializing the input to hidden matrix
        self.v = self.init_weight(V,D)
        dv = np.zeros((V,D))
        v = self.v
        #initializing the hidden to output matrix
        self.u = self.init_weight(D,V)
        du = np.zeros((D,V))
        u = self.u
        
        Y  = X + [1] 
        X = [0] + X
        
        batchSize = 10
        batchIterations = len(X)/batchSize
        costs = []
        for i in xrange(batchIterations):
            #this is Vc
            xBatch = X[i*batchSize:i*batchSize + batchSize]
            #this is Vw
            yBatch = Y[i*batchSize:i*batchSize +  batchSize]
            
            #v is v*d matrix
            #h is n*d vector
            h = v[xBatch]
            #u is d*v matrix
            softmax_numerator_y = np.exp(np.dot(h,u))
            print softmax_numerator_y
            
            sum_y = np.sum(softmax_numerator_y,axis=1,keepdims=True)
            
            softmax = (softmax_numerator_y)/sum_y
            
            #cost calculation
            cost = -1*np.mean(np.log(softmax[np.arange(softmax.shape[0]),yBatch]))
            
            print cost
            costs.append(cost)
            
            #backpropagation
            #vw calculation
            grad1 = np.transpose(v[xBatch,:]) - np.transpose(softmax[np.arange(softmax.shape[0]),yBatch].reshape(-1,1)*v[xBatch,:])
            #vc calculation
            grad2 = np.transpose(u[:,yBatch]) - softmax.dot(np.transpose(u))
            print grad1
            #vw calculation
            u[:,yBatch] += mu*du[:,yBatch] - alpha*grad1 
            #vc calculation
            v[xBatch,:] += mu*dv[xBatch,:] - alpha*grad2
            
            dv = np.zeros((V,D))
            du = np.zeros((D,V))
            
            du[:,yBatch] = grad1
            dv[xBatch,:] = grad2
        plt.plot(costs)
            
            
            

In [177]:
bg = bigram(D,V)
bg.fit(sentences)

[[  5.12831528e-06   1.46283978e+04   3.95668033e-07 ...,   5.35162069e+10
    1.33518993e+01   7.24327184e-05]
 [  2.23641522e+04   6.07250442e-02   2.86308136e-02 ...,   1.02699047e-01
    4.37636010e+00   1.00640350e+04]
 [  4.44927976e+11   7.76861238e+02   8.87204383e-04 ...,   2.08520870e+01
    3.62367223e-02   1.24946186e+13]
 ..., 
 [  1.54282869e+08   1.90245087e+02   1.94645369e+07 ...,   1.00431635e-03
    1.59239406e+02   1.64465182e+04]
 [  1.39813615e+12   4.45342074e-02   5.98250183e-01 ...,   3.58315655e+04
    2.50947947e-02   1.23751443e+02]
 [  5.70797070e+05   1.02894231e-02   1.45610170e+01 ...,   6.37559879e+01
    2.07970956e-01   2.30853761e-09]]
37.4623190605
[[  7.66879045e-01   4.21519840e-01  -5.43342206e-01  -1.81106538e+00
   -1.30034949e+00  -1.12779029e+00   1.65908043e+00   1.89085229e+00
   -1.25293935e+00   1.76786705e-01]
 [  7.80243409e-03   2.15950740e+00   3.55972979e-01   5.23982669e-01
   -8.99017227e-01   1.41610545e-01  -3.65903459e-01   7.01

[[ -2.60952301e-01   2.39433739e-01  -2.60952301e-01  -3.48719459e-01
   -5.77104703e-01   8.84403341e-01  -7.64269884e-01  -9.56018635e-01
    2.39310580e+00  -5.26930323e-01]
 [ -9.86459855e-01   3.15408581e-01  -9.86459855e-01  -9.91156627e-01
    1.80547827e+00   1.50772466e-01   4.92740937e-01  -2.07839483e-01
    2.90075963e-01  -6.25980989e-01]
 [ -2.95021011e-01   7.46038733e-01  -2.95021011e-01  -1.47237108e-01
    1.10713601e+00  -9.01166142e-01  -2.75874385e-01   9.81766443e-01
    2.06891599e+00   1.01360254e+00]
 [ -1.27588273e-02   1.14017633e+00  -1.27588273e-02  -5.60034605e-01
   -7.46349999e-01  -8.94702502e-01   6.65122387e-02   1.25645530e+00
    1.81486180e+00  -1.47028938e+00]
 [ -4.36395363e-01   3.27513516e-01  -4.36395363e-01  -5.26110209e-02
   -7.86386883e-01   1.05294708e+00   6.88227732e-01  -9.78912067e-01
   -8.47679555e-01  -6.26828162e-01]
 [ -8.01785102e-01   1.41675787e+00  -8.01785102e-01   3.26552166e-02
    8.68157356e-02  -1.01836903e+00  -1.97645

[[  1.09370155e+05   3.88408185e+05   3.29545520e+07 ...,   4.00931229e+02
    1.30532821e-10   2.83298268e-01]
 [  4.11352157e-03   2.37591129e-01   8.35271829e+08 ...,   8.59352114e+01
    1.13511458e+05   7.16304426e-07]
 [  1.77816083e-09   2.84197861e+02   5.76107981e-03 ...,   5.76696563e+03
    4.56962320e-09   1.45741047e-05]
 ..., 
 [  1.07870214e+04   2.16472424e-04   5.93170305e+03 ...,   3.98464077e+07
    3.59127960e+04   7.02499565e-07]
 [  5.16720251e-05   3.33091766e-08   1.73987489e+02 ...,   4.21657373e-05
    6.38051542e-06   1.15145753e+11]
 [  4.48586559e+00   2.95163012e+07   7.78840703e-02 ...,   4.86786051e-01
    5.38860548e+00   2.18651131e-06]]
47.6814251245
[[ -9.74954352e-01   9.59418889e-02  -9.81226769e-01   4.20058489e-01
    9.56161858e-01   7.96534467e-01   1.62942500e+00   1.38545669e+00
   -6.23181577e-01   2.18386913e-02]
 [ -1.28441274e+00  -1.10622199e+00   7.09389409e-02  -1.85472739e-01
   -1.11751637e+00  -4.33344588e-01   6.17517097e+00   8.87

[[ -1.12705444e+00   3.02641504e+00   1.19338517e+00  -2.90322026e-01
   -6.21946631e-01   1.28822558e+00  -8.64913912e-01   1.89192296e+00
    1.25232781e+00  -1.20470730e+00]
 [ -1.04380222e+00  -9.75662894e-01  -1.11920273e+00   1.52044581e+00
    3.52360903e+00  -8.53799821e-01   2.29611927e-01   3.21933582e-01
    6.72139793e-01  -1.52189572e+00]
 [  5.45752267e-01  -3.85399771e-01   1.23886693e+00   8.05713007e-01
    1.79443951e+00   1.30962522e+00  -3.90239776e-02   8.49841543e-01
   -1.34351680e+00   2.41393109e-01]
 [  4.67804903e-01   1.60949623e+00   8.52959051e-02   4.18663284e-01
    1.40006061e-01  -2.70489363e-01  -4.31420067e-01   9.32016334e-01
    7.77956102e-01   1.21997606e+00]
 [ -1.79632713e-01   8.95382013e-01   1.22167200e+00  -2.52488606e-01
   -2.93845240e+00   5.11688336e-02   1.01644815e+00  -7.05414804e-02
    1.26197749e+00   5.07814690e-02]
 [  1.24996028e+00   3.30769143e-02   7.00865486e-01  -7.10622514e-01
   -6.50482053e-01   5.51781355e-01  -7.66414

[[  5.70261621e-07   3.98675728e-06   2.72462708e+15 ...,   1.16748313e-04
    3.33055124e-11   3.41742481e+01]
 [  2.47285572e+03   3.08318802e+10   4.08585940e-07 ...,   2.09188135e+02
    6.38359609e-04   1.03944100e+00]
 [  1.44356954e+01   6.88915687e-06   7.27719246e-05 ...,   7.42470677e+00
    1.53235484e+07   8.28281600e+00]
 ..., 
 [  2.38618000e-06   6.43205417e-05   5.71711365e-01 ...,   4.90844997e-01
    1.87320214e+07   3.59059387e-04]
 [  2.61144497e-05   9.84979365e+00   2.17004624e-03 ...,   5.58410973e+02
    7.48568263e+06   2.77650094e-05]
 [  6.43978976e-10   4.78273481e-01   6.15929442e-01 ...,   4.97726619e-02
    3.83650697e+01   4.49454581e-04]]
43.8403750427
[[ -1.72167699e+00   1.27412428e+00   7.16285034e-01   1.81747482e+00
   -3.49188048e-01   3.00619225e+00  -1.24947593e+00   6.69440963e-02
   -5.54798696e-01  -8.06262645e-01]
 [ -1.19531302e+00  -2.47111089e-01  -4.15796610e-01  -1.33879858e+00
   -9.91400409e-01  -1.47243126e-01  -1.27604448e+00  -5.66

...

[[ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan

[[ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan

[[ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan

[[ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan  nan]
 [ nan  nan  nan  nan  nan  nan  nan  nan  nan

KeyboardInterrupt: 

In [45]:
a = np.ones((3,1))

In [50]:
a = np.arange(4).reshape(-1,1)

In [55]:
b = np.vstack(([1,2,3,4],[1,2,3,4],[1,2,3,4],[1,2,3,4]))

In [68]:
y = a*b

array([1, 4, 9])

In [97]:
y

array([[ 0,  0,  0,  0],
       [ 1,  2,  3,  4],
       [ 2,  4,  6,  8],
       [ 3,  6,  9, 12]])